# Assignment 5 - Text Analysis
An explanation this assignment could be found in the .pdf explanation document


## Materials to review for this assignment
<h4>From Moodle:</h4> 
<h5><u>Review the notebooks regarding the following python topics</u>:</h5>
<div class="alert alert-info">
&#x2714; <b>Working with strings</b> (tutorial notebook)<br/>
&#x2714; <b>Text Analysis</b> (tutorial notebook)<br/>
&#x2714; <b>Hebrew text analysis tools (tokenizer, wordnet)</b> (moodle example)<br/>
&#x2714; <b>(brief review) All previous notebooks</b><br/>
</div> 
<h5><u>Review the presentations regarding the following topics</u>:</h5>
<div class="alert alert-info">
&#x2714; <b>Text Analysis</b> (lecture presentation)<br/>
&#x2714; <b>(brief review) All other presentations</b><br/>
</div>

## Preceding Step - import modules (packages)
This step is necessary in order to use external modules (packages). <br/>

In [1]:
# --------------------------------------
import pandas as pd
import numpy as np
# --------------------------------------


# --------------------------------------
# ------------- visualizations:
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
# --------------------------------------


# ---------------------------------------
import sklearn
from sklearn import preprocessing, metrics, pipeline, model_selection, feature_extraction 
from sklearn import naive_bayes, linear_model, svm, neural_network, neighbors, tree
from sklearn import decomposition, cluster

from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV 
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.metrics import mean_squared_error, r2_score, silhouette_score
from sklearn.preprocessing import MinMaxScaler, StandardScaler, LabelEncoder

from sklearn.svm import LinearSVC
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import Perceptron, SGDClassifier
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.naive_bayes import MultinomialNB, GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
# ---------------------------------------


# ----------------- output and visualizations: 
import warnings
from sklearn.exceptions import ConvergenceWarning
warnings.simplefilter("ignore")
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter("ignore", category=ConvergenceWarning)
# show several prints in one cell. This will allow us to condence every trick in one cell.
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
%matplotlib inline
pd.pandas.set_option('display.max_columns', None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)
# ---------------------------------------

### Text analysis and String manipulation imports:

In [2]:
# --------------------------------------
# --------- Text analysis and Hebrew text analysis imports:
# vectorizers:
from sklearn.feature_extraction import text
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

# regular expressions:
import re
# --------------------------------------

### (optional) Hebrew text analysis - WordNet (for Hebrew)
Note: the WordNet is not a must

#### (optional) Only if you didn't install Wordnet (for Hebrew) use:

In [3]:
# word net installation:

# unmark if you want to use and need to install
#!pip install wn
#!python -m wn download omw-he:1.4

In [4]:
# word net import:

# unmark if you want to use:
import wn

### (optional) Hebrew text analysis - hebrew_tokenizer (Tokenizer for Hebrew)
Note: the hebrew_tokenizer is not a must

#### (optional) Only if you didn't install hebrew_tokenizer use:

In [5]:
# Hebrew tokenizer installation:

# unmark if you want to use and need to install:
#!pip install hebrew_tokenizer

In [6]:
# Hebrew tokenizer import:

# unmark if you want to use:
import hebrew_tokenizer as ht

C:\Users\royi5\Desktop\assignment5-text_analysis


### Reading input files
Reading input files for train annotated corpus (raw text data) corpus and for the test corpus

In [7]:
train_filename = 'annotated_corpus_for_train.csv'
test_filename  = 'corpus_for_test.csv'
df_train = pd.read_csv(train_filename, index_col=None, encoding='utf-8')
df_test  = pd.read_csv(test_filename, index_col=None, encoding='utf-8')

In [8]:
df_train.head(8)
df_train.shape

story gender
0  כשחבר הזמין אותי לחול, לא באמת חשבתי שזה יקרה,...      m
1  לפני שהתגייסתי לצבא עשיתי כל מני מיונים ליחידו...      m
2  מאז שהתחילו הלימודים חלומו של כל סטודנט זה הפנ...      f
3  כשהייתי ילד, מטוסים היה הדבר שהכי ריתק אותי. ב...      m
4  ‏הייתי מדריכה בכפר נוער ומתאם הכפר היינו צריכי...      f
5  לפני כ3 חודשים טסתי לרומא למשך שבוע. טסתי במטו...      f
6  אני כבר שנתיים נשוי והשנה אני ואישתי סוף סוף י...      m
7  השנה התחלנו שיפוץ בדירה שלנו בתל אביב. הדירה ה...      f

(753, 2)

In [9]:
df_test.head(3)
df_test.shape

test_example_id                                              story
0                0  כל קיץ אני והמשפחה נוסעים לארצות הברית לוס אנג...
1                1  הגעתי לשירות המדינה אחרי שנתיים כפעיל בתנועת "...
2                2  אחת האהבות הגדולות שלי אלו הכלבים שלי ושל אישת...

(323, 2)

### Your implementation:
Write your code solution in the following code-cells

In [10]:
if df_train['gender'].dtype == 'object':
    df_train['gender'] = df_train['gender'].map({'f': 0, 'm': 1})
df_train.head(8)

story  gender
0  כשחבר הזמין אותי לחול, לא באמת חשבתי שזה יקרה,...       1
1  לפני שהתגייסתי לצבא עשיתי כל מני מיונים ליחידו...       1
2  מאז שהתחילו הלימודים חלומו של כל סטודנט זה הפנ...       0
3  כשהייתי ילד, מטוסים היה הדבר שהכי ריתק אותי. ב...       1
4  ‏הייתי מדריכה בכפר נוער ומתאם הכפר היינו צריכי...       0
5  לפני כ3 חודשים טסתי לרומא למשך שבוע. טסתי במטו...       0
6  אני כבר שנתיים נשוי והשנה אני ואישתי סוף סוף י...       1
7  השנה התחלנו שיפוץ בדירה שלנו בתל אביב. הדירה ה...       0

In [11]:
X = df_train.iloc[:, :-1] 
y = df_train.iloc[:, -1].to_frame()


# Creating tokenizer:
The hebrew tokenizer splits the words into cateogries like: punctuation, white space and HEBREW.
since i want to classify if the write is male or female, i have no use for all categories except the Hebrew words.
therfore, my_tokenizer returns only the hebrew words.

In [12]:
def my_tokenizer(text):
    tokens = ht.tokenize(text)
    words = [token[1] for token in tokens if token[0] == 'HEBREW']
    return words

# countVectorizer:
I used my_tokenizer and the countvectorizer with max_features of 10,000 words to create the following dataframe

In [13]:
vec = CountVectorizer(tokenizer=my_tokenizer,max_features=10000)
X_trainCV = vec.fit_transform(X['story'])
X_trainCV.toarray()
df_after_tokenizer=pd.DataFrame(X_trainCV.toarray(), columns=vec.get_feature_names_out())
df_after_tokenizer


array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [2, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

א  אבא  אבבה  אבטלה  אבי  אביב  אביה  אבל  אבן  אבק  אגב  אגודת  אגיע  \
0    0    0     0      0    0     0     0    4    0    0    0      0     0   
1    0    0     0      0    0     0     0    1    0    0    0      0     0   
2    0    0     0      0    0     0     0    5    0    0    0      0     0   
3    0    5     0      0    0     0     0    2    0    0    0      0     0   
4    0    0     0      0    0     0     0    2    0    0    0      0     0   
..  ..  ...   ...    ...  ...   ...   ...  ...  ...  ...  ...    ...   ...   
748  0    0     0      0    0     0     0    0    0    0    0      0     0   
749  0    0     0      0    0     0     0    3    0    0    0      0     0   
750  0    0     0      0    0     0     0    2    0    0    0      0     0   
751  2    0     0      0    0     0     0    0    0    0    0      0     0   
752  0    0     0      0    0     0     0    2    0    0    0      0     0   

     אגם  אדום  אדומה  אדומות  אדון  אדם  אדמה  אה  אהב  אהבה  אהבו  אהבנו  \
0      1     0      0       0     0    0     0   0    0     0     0      0   
1      0     0      0       0     0    3     0   0    0     0     0      0   
2      0     0      0       0     0    0     0   0    0     0     0      0   
3      0     0      0       0     0    1     0   0    0     0     0      0   
4      0     0      0       0     0    0     0   0    0     0     0      0   
..   ...   ...    ...     ...   ...  ...   ...  ..  ...   ...   ...    ...   
748    0     0      0       0     0    1     0   0    0     0     0      0   
749    0     0      0       0     0    0     0   0    0     0     0      0   
750    0     0      0       0     0    0     0   0    0     0     0      0   
751    0     0      0       0     0    0     0   0    0     0     0      0   
752    0     0      0       0     0    0     0   0    0     0     0      0   

     אהבתי  אהיה  או  אוגוסט  אודות  אודישן  אודם  אוהב  אוהבים  אוהבת  אוהד  \
0        0     0   0       0      0       0     0     0       0      0     0   
1        0     0   0       0      0       0     0     1       0      0     0   
2        0     0   0       0      0       0     0     0       0      0     0   
3        0     0   0       0      0       0     0     0       0      0     0   
4        0     0   1       0      0       0     0     0       0      0     0   
..     ...   ...  ..     ...    ...     ...   ...   ...     ...    ...   ...   
748      0     0   1       0      0       0     0     0       0      0     0   
749      0     0   2       1      0       0     0     0       0      0     0   
750      0     0   0       0      0       0     0     0       0      0     0   
751      0     0   1       1      0       0     0     0       0      0     0   
752      0     0   0       0      0       0     0     0       0      0     0   

     אוהדי  אוהדים  אוהל  אוהלים  אוויר  אווירה  אוטו  אוטובוס  אוטובוסים  \
0        0       0     0       0      0       0     0        0          0   
1        0       0     1       0      0       0     0        0          0   
2        0       0     0       0      0       0     0        0          0   
3        0       0     0       0      0       0     0        0          0   
4        0       0     0       0      0       0     0        0          0   
..     ...     ...   ...     ...    ...     ...   ...      ...        ...   
748      0       0     0       0      0       0     0        0          0   
749      0       0     0       0      3       0     0        0          0   
750      0       0     0       0      0       0     0        0          0   
751      0       0     0       0      0       0     0        0          0   
752      0       0     0       0      0       0     0        0          0   

     אוטומטי  אוטומציה  אוי  אוירה  אוכל  אוכלים  אוכלת  אולי  אולם  אולמות  \
0          0         0    0      0     0       0      0     0     0       0   
1          0         0    0      0     0       0      0     0     0       0   
2       

# TfidfVectorizer

In [14]:
vec = TfidfVectorizer(tokenizer=my_tokenizer,max_features=10000)
X_trainIDF = vec.fit_transform(df_train['story'])
df_after_tfidf=pd.DataFrame(X_trainIDF.toarray(), columns=vec.get_feature_names_out())


# normalized

In [15]:
count_vect = CountVectorizer(tokenizer=my_tokenizer,max_features=10000)
X_train_counts = count_vect.fit_transform(df_train['story'])
X_train_normalized = preprocessing.normalize(X_train_counts, norm='l1')
X_train_normalized.shape


(753, 10000)

# Machine learning:
I decided to use 6 types of machine learnings in my project:<br>
MLP-Multilayer Perceptron<br>
DT- Decision Tree<br>
KNN- K Nearest Neighbors<br>
Linear SVC- Linear Support Vector Machine<br>
MNB- Multinomial Naive Bayes

# Pipelines:
In order to be more efficient in my machine learning progress i used pipeline that contain the count vectorizer, the normalizer and the machine learning algorithm<br>
the hyper parameters i chose for each algorithm are based on grid search ive done later in the code.

In [16]:
pipelines = [ 
    
    ('MLP', Pipeline([        
        ('vect', CountVectorizer(tokenizer=my_tokenizer, max_features=10000)),        
        ('norm', preprocessing.Normalizer(norm='l1')),        
        ('clf', MLPClassifier(activation='tanh',hidden_layer_sizes=(50,50)))    
    ])),
    
    ('DT', Pipeline([
        ('vect', CountVectorizer(tokenizer=my_tokenizer, max_features=10000, ngram_range=(2, 4))),
        ('norm', preprocessing.Normalizer(norm='l1')),
        ('clf', DecisionTreeClassifier(criterion='gini',max_depth=30,min_samples_leaf=1,
                                       min_samples_split=2,random_state=42))
    ])),
    
    ('KNN', Pipeline([
        ('vect', CountVectorizer(tokenizer=my_tokenizer, max_features=10000)),
        ('norm', preprocessing.Normalizer(norm='l1')),
        ('clf', KNeighborsClassifier(weights='distance'))
    ])),
    
    ('SVC', Pipeline([
        ('vect', CountVectorizer(tokenizer=my_tokenizer, max_features=10000)),
        ('norm', preprocessing.Normalizer(norm='l1')),
        ('clf', LinearSVC(C=0.1,random_state=42))
    ])),
    
    ('Perceptron', Pipeline([
        ('vect', CountVectorizer(tokenizer=my_tokenizer, max_features=10000)),
        ('norm', preprocessing.Normalizer(norm='l1')),
        ('clf', Perceptron(alpha=0.0001,max_iter=1000))
    ])),
    
    ('MNB', Pipeline([
        ('vect', CountVectorizer(tokenizer=my_tokenizer, max_features=10000)),
        ('norm', preprocessing.Normalizer(norm='l1')),
        ('clf', MultinomialNB(alpha=0.01,fit_prior=False))
    ]))
]

for name, pipeline in pipelines:
    scores = cross_val_score(pipeline, X['story'], y['gender'], cv=10, scoring='f1_macro')
    print("Cross-validation scores on {}: {}".format(name, scores))
    print("Average cross-validation score on {}: {:.2f}".format(name, scores.mean()))
    

Cross-validation scores on MLP: [0.65364583 0.60416667 0.61577351 0.688      0.61485793 0.592
 0.61485793 0.61485793 0.67431762 0.53846154]
Average cross-validation score on MLP: 0.62
Cross-validation scores on DT: [0.59517802 0.69690927 0.63228928 0.70862471 0.57091238 0.78632479
 0.66124661 0.66124661 0.61371645 0.60480094]
Average cross-validation score on DT: 0.65
Cross-validation scores on KNN: [0.52167832 0.44944882 0.57482517 0.47397564 0.59615385 0.53846154
 0.58471761 0.51215337 0.57386364 0.58471761]
Average cross-validation score on KNN: 0.54
Cross-validation scores on SVC: [0.43283582 0.43283582 0.43283582 0.43609023 0.43609023 0.43181818
 0.43181818 0.43181818 0.43181818 0.43181818]
Average cross-validation score on SVC: 0.43
Cross-validation scores on Perceptron: [0.5546875  0.56221198 0.73660357 0.61485793 0.61371645 0.62779156
 0.58126551 0.592      0.70833333 0.75158085]
Average cross-validation score on Perceptron: 0.63
Cross-validation scores on MNB: [0.43283582 0.42

# Grid Search:
in the grid search i tried to use many hyperparameters and many options for them in order to improve my results.<br>
the whole process of this grid search takes few hours, therefore i ran it once, got the best parameters and used it directly in the algorithm function and left only the max features parameter to be checked 

In [17]:
param_grids = [
    {
        'vect__max_features': [1000, 5000, 10000],
#         'clf__hidden_layer_sizes': [(50,), (100,), (50, 50), (100, 100)],
#         'clf__activation': ['relu', 'tanh']
    },  # MLPClassifier

    {
        'vect__max_features': [1000, 5000, 10000],
#         'clf__criterion': ['gini', 'entropy'],
#         'clf__max_depth': [10, 20, 30, None],
#         'clf__min_samples_split': [2, 5, 10],
#         'clf__min_samples_leaf': [1, 2, 4]
    },  # DecisionTreeClassifier

    {
        'vect__max_features': [1000, 5000, 10000],
#         'clf__n_neighbors': [5, 10, 20],
#         'clf__weights': ['uniform', 'distance'],
#         'clf__algorithm': ['auto', 'ball_tree', 'kd_tree', 'brute']
    },  # KNeighborsClassifier

    {
        'vect__max_features': [1000, 5000, 10000],
#         'clf__C': [0.1, 1, 10],
#         'clf__penalty': ['l1', 'l2'],
#         'clf__loss': ['hinge', 'squared_hinge']
    },  # LinearSVC

    {
        'vect__max_features': [1000, 5000, 10000],
#         'clf__alpha': [0.0001, 0.001, 0.01],
#         'clf__penalty': ['l1', 'l2', 'elasticnet'],
#         'clf__max_iter': [1000, 5000, 10000]
    },  # Perceptron

    {
        'vect__max_features': [1000, 5000, 10000],
#         'clf__alpha': [0.01, 0.1, 1],
#         'clf__fit_prior': [True, False]
    }  # MultinomialNB
]



In [18]:
fitted_models = []

for i, (name, pipeline) in enumerate(pipelines):
    print("Grid search results for {}".format(name))
    param_grid = param_grids[i]
    grid_search = GridSearchCV(pipeline, param_grid=param_grid, cv=10, scoring='f1_macro')
    grid_search.fit(X['story'], y['gender'])
    print("Best parameters found: {}".format(grid_search.best_params_))
    print("Best cross-validation score: {:.2f}".format(grid_search.best_score_))
    print("Detailed results:")
    means = grid_search.cv_results_['mean_test_score']
    stds = grid_search.cv_results_['std_test_score']
    for mean, std, params in zip(means, stds, grid_search.cv_results_['params']):
        print("{:.2f} (+/-{:.2f}) for {}".format(mean, std * 2, params))
    print("==================================================")
    
    fitted_models.append(grid_search.best_estimator_)

Grid search results for MLP


GridSearchCV(cv=10,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(max_features=10000,
                                                        tokenizer=<function my_tokenizer at 0x0000029C58955000>)),
                                       ('norm', Normalizer(norm='l1')),
                                       ('clf',
                                        MLPClassifier(activation='tanh',
                                                      hidden_layer_sizes=(50,
                                                                          50)))]),
             param_grid={'vect__max_features': [1000, 5000, 10000]},
             scoring='f1_macro')

Best parameters found: {'vect__max_features': 1000}
Best cross-validation score: 0.67
Detailed results:
0.67 (+/-0.09) for {'vect__max_features': 1000}
0.62 (+/-0.10) for {'vect__max_features': 5000}
0.62 (+/-0.07) for {'vect__max_features': 10000}
Grid search results for DT


GridSearchCV(cv=10,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(max_features=10000,
                                                        ngram_range=(2, 4),
                                                        tokenizer=<function my_tokenizer at 0x0000029C58955000>)),
                                       ('norm', Normalizer(norm='l1')),
                                       ('clf',
                                        DecisionTreeClassifier(max_depth=30,
                                                               random_state=42))]),
             param_grid={'vect__max_features': [1000, 5000, 10000]},
             scoring='f1_macro')

Best parameters found: {'vect__max_features': 10000}
Best cross-validation score: 0.65
Detailed results:
0.55 (+/-0.09) for {'vect__max_features': 1000}
0.64 (+/-0.13) for {'vect__max_features': 5000}
0.65 (+/-0.12) for {'vect__max_features': 10000}
Grid search results for KNN


...

Best parameters found: {'vect__max_features': 1000}
Best cross-validation score: 0.43
Detailed results:
0.43 (+/-0.00) for {'vect__max_features': 1000}
0.43 (+/-0.00) for {'vect__max_features': 5000}
0.43 (+/-0.00) for {'vect__max_features': 10000}
Grid search results for Perceptron


GridSearchCV(cv=10,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(max_features=10000,
                                                        tokenizer=<function my_tokenizer at 0x0000029C58955000>)),
                                       ('norm', Normalizer(norm='l1')),
                                       ('clf', Perceptron())]),
             param_grid={'vect__max_features': [1000, 5000, 10000]},
             scoring='f1_macro')

Best parameters found: {'vect__max_features': 5000}
Best cross-validation score: 0.65
Detailed results:
0.63 (+/-0.12) for {'vect__max_features': 1000}
0.65 (+/-0.19) for {'vect__max_features': 5000}
0.63 (+/-0.14) for {'vect__max_features': 10000}
Grid search results for MNB


GridSearchCV(cv=10,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(max_features=10000,
                                                        tokenizer=<function my_tokenizer at 0x0000029C58955000>)),
                                       ('norm', Normalizer(norm='l1')),
                                       ('clf',
                                        MultinomialNB(alpha=0.01,
                                                      fit_prior=False))]),
             param_grid={'vect__max_features': [1000, 5000, 10000]},
             scoring='f1_macro')

Best parameters found: {'vect__max_features': 1000}
Best cross-validation score: 0.67
Detailed results:
0.67 (+/-0.09) for {'vect__max_features': 1000}
0.59 (+/-0.11) for {'vect__max_features': 5000}
0.48 (+/-0.07) for {'vect__max_features': 10000}


# Trying the model on the Test file:
I created dataframe that contains all types of machine learning i used as columns and the predicted label as the value

In [21]:
predicted_labels = []

for model in fitted_models:
    predicted_label = model.predict(df_test['story'])
    predicted_labels.append(predicted_label)

df_predictions = pd.DataFrame({
    'test_example_id': df_test['test_example_id'],
    'DT': predicted_labels[0],
    'MNB': predicted_labels[1],
    'MLP': predicted_labels[2],
    'Perceptron': predicted_labels[3],
    'KNN': predicted_labels[4],
    'SVC': predicted_labels[5]
})


label_map = {1: 'm', 0: 'f'}

df_predictions['DT'] = df_predictions['DT'].map(label_map)
df_predictions['MNB'] = df_predictions['MNB'].map(label_map)
df_predictions['MLP'] = df_predictions['MLP'].map(label_map)
df_predictions['Perceptron'] = df_predictions['Perceptron'].map(label_map)
df_predictions['KNN'] = df_predictions['KNN'].map(label_map)
df_predictions['SVC'] = df_predictions['SVC'].map(label_map)


df_predictions.head(5)
df_predictions.tail(5)

test_example_id DT MNB MLP Perceptron KNN SVC
0                0  m   m   m          m   m   m
1                1  m   m   m          m   m   m
2                2  m   m   f          m   m   m
3                3  m   m   f          m   m   m
4                4  f   m   m          m   f   m

test_example_id DT MNB MLP Perceptron KNN SVC
318              318  m   m   m          m   m   m
319              319  m   f   m          m   m   m
320              320  m   m   m          m   m   m
321              321  m   m   m          m   m   m
322              322  m   m   m          m   m   m

### Save output to csv (optional)
After you're done save your output to the 'classification_results.csv' csv file.<br/>
We assume that the dataframe with your results contain the following columns:
* column 1 (left column): 'test_example_id'  - the same id associated to each of the test stories to be predicted.
* column 2 (right column): 'predicted_category' - the predicted gender value for each of the associated story. 

Assuming your predicted values are in the `df_predicted` dataframe, you should save you're results as following:

In [20]:
#df_predicted.to_csv('classification_results.csv',index=False)